# Programmation éco-responsable

Marc Lorenzi

11 juin 2024

In [ ]:
import math, sys, time

In [ ]:
class Compteur:
    
    def __init__(self): self.val = 0
    def reset(self): self.val = 0
    def incr(self, c): self.val += c

In [ ]:
cptr0 = Compteur()

Lorsqu'on exécute un programme sur une machine, celle-ci utilise des *ressources*. Quels types de ressources ? Combien de ressources ? C'est l'objet de la *théorie de la complexité*. 

Il existe de nombreux types de ressources. Pour n'en citer que trois, le *temps*, *l'espace* et *l'énergie*.

- la complexité en temps, c'est ce que ressent l'utilisateur lorsqu'il trépigne devant sa machine en attendant la réponse de l'algorithme. La machine n'y est pas sensible, elle n'est pas pressée. L'utilisateur, si.
- la complexité en espace, c'est ce que ressent la machine lorsqu'elle voit sa mémoire disponible se réduire, se réduire, se réduire. L'utilisateur n'y est pas sensible. Sauf lorsqu'il n'y a plus de mémoire disponible et que la machine plante.
- la complexité en énergie, c'est ce que ressent mon portefeuille quand arrive la facture d'électricité. Le lecteur intéressé pourra par exemple consulter l'article 

Demaine, Erik D., Jayson Lynch, Geronimo J. Mirano, and Nirvan Tyagi. “Energy- Efficient Algorithms.” Proceedings of the 2016 ACM Conference on Innovations in Theoretical Computer Science - ITCS ’16 (2016), Cambridge, Massachusetts, USA, January 14-17, 2016, pp. 321-332.

En voici deux courts extraits.

<p style="border: 1px solid black; padding: 10px;background-color:#FFDDDD;border-radius:10px;" >
    <b>Landauer limit</b>. CPU power efficiency (number of computations per kilowatt hour of energy) has doubled every 1.57 years from 1946 to 2009. Within the next 15–60 years, however, this trend will hit a fundamental limit in physics, known as Landauer’s Principle. This principle states that discarding one bit of information (increasing the entropy of the environment by one bit) requires $kT \ln 2$ energy, where $k$ is Boltzmann’s constant and $T$ is ambient temperature, which is about $2.8 · 10^{−21}$ joules or $7.8 · 10^{−28}$ kilowatt hours at room temperature (20◦C). (Even at liquid nitrogen temperatures, this requirement goes down by less than a factor of 5.) Physics has proved this principle under a variety of different assumptions, and it has also been observed experimentally.<br><br>
Most CPUs discard many bits of information per clock cycle, as much as one per gate; for example, an AND gate with output 0 or an OR gate with output 1 “forgets” the exact values of its inputs. To see how this relates to Landauer’s principle, consider the state-of-the-art 15-core Intel Xeon E7-4890 v2 2.8GHz CPU. In a 4-processor configuration, it achieves $1.2 · 10^{12}$ computations per second at 620 watts,1 for a ratio of $7.4 · 10^{15}$ computations per kilowatt hour. At the pessimistic extreme, if every one of the $4.3 · 10^9$ transistors discards a bit, then the product $3.2 · 10^{25}$ is only three orders of magnitude greater than Landauer limit. If CPUs continue to double in energy efficiency every 1.57 years, this gap will close in less than 18 years. At the more optimistic extreme, if a 64-bit computation discards only 64 bits (to overwrite one register), the gap will close within 59 years. The truth is probably somewhere in between these extremes.<br><br>
...<br><br>
<b>Consequences</b>. Reducing the energy consumption of many computations by several orders of magnitude will have tremendous impact on practice. Computer servers alone constitute 23– 31 gigawatts of power consumption, which translates to $\$$ 14–18 billion annually and 1.1–1.5% of worldwide electricity use; there are roughly 50 times as many PCs with an annual growth rate of 12%; and there are about as many smartphones as PCs. Improved energy efficiency would save both environmental impact and money. Reducing energy consumption would also improve the longevity of batteries in portable devices (laptops, phones, watches, etc.), or enable the use of smaller and lighter batteries for similar performance. Perhaps most interestingly, lower energy consumption would lead to faster CPUs, as cooling is the main bottleneck in increasing clock speeds; reducing the energy consumption by a factor of $\alpha$, we expect to be able to run the CPU roughly $\alpha$ times faster. For example, the world record for CPU clock speed of 8.429 GHz was set by AMD with liquid nitrogen cooling.
</p>

Dans ce notebook, nous allons écrire quelques fonctions calculant le nombre de *dérangements* d'un ensemble fini et nous allons comparer leurs complexités en temps (et parfois en espace).

<p style="border: 1px solid black; padding: 10px;background-color:#FFFFCC;border-radius:10px;" >
    <b>Définition 1.</b> Un <i>dérangement</i> de l'ensemble $E$ est une bijection $\sigma\in\mathfrak S(E)$ telle que pour tout $x\in E$, $\sigma(x)\ne x$.
</p>

Si $E$ est fini, de cardinal $n$, le nombre de dérangements de $E$ ne dépend que de $n$. Notons-le $d_n$.

## 1. La relation de récurrence

<p style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;border-radius:10px;" >
    <b>Proposition 1 (récurrence).</b> <br><br>
    $d_0=1$, $d_1=0$ et pour tout $n\in\mathbb N$,$d_{n+2}=(n+1)(d_{n+1}+d_n)$.
</p>

### 1.1 Récursivité naïve

Écrire une fonction récursive naïvement à partir de cette relation de récurrence est une mauvaise idée. Écrivons-la quand même, pour voir que c'est *vraiment* une *très très* mauvaise idée.

In [ ]:
def nb_der1(n, cptr=cptr0):
    if n == 0: return 1
    elif n == 1: return 0
    else:
        cptr.incr(3)
        return (n - 1) * (nb_der1(n - 1) + nb_der1(n - 2))

In [ ]:
for n in range(11):
    print('%3d%10d' % (n, nb_der1(n)))

Bon, et alors ? Ça marche, non ? Certes, mais obtenir la valeur de $d_{10}$ n'est pas un grand prodige. On est loin du Turing Award (et du million de dollars offerts pour ce prix annuel).

Notons $C_n$ le nombre d'opérations arithmétiques effectuées lors de l'appel `nb_der1(n)`. On a $C_0=C_1=0$ et pour tout $n\ge 2$,

$$C_n=C_{n-1}+C_{n-2}+3$$

Soit $(F_n)_{n\in \mathbb N}$ la suite de Fibonacci définie par $F_0=0$, $F_1=1$ et pour tout $n\in\mathbb N$, $F_{n+2}=F_{n+1}+F_n$. 

<p style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;border-radius:10px;" >
    <b>Proposition 2.</b> Pour tout $n\in\mathbb N$, $C_n=3F_{n+1}-3$.
</p>

**Démonstration.** Par récurrence à deux termes sur $n$. On a $C_0=0=3F_1-3$ et $C_1=0=3F_2-3$. Soit $n\in\mathbb N$. Supposons $C_n=3F_{n+1}-3$ et $C_{n+1}=3F_{n+2}-3$. On a alors

$$C_{n+2}=C_{n+1}+C_n+3=(3F_{n+1}-3)+(3F_{n+2}-3)+3=3(F_{n+1}+F_{n+2})-3=3F_{n+3}-3$$

Remarquons que $F_n\sim \varphi^n/\sqrt 5$ où $\varphi=(1+\sqrt 5)/2$. On a donc

$$C_n\sim \frac{3\varphi^{n+1}}{\sqrt 5}$$

La complexité de `nb_der1` est ainsi ... exponentielle.

L'approximation ci-dessus est très bonne : l'erreur commise est 

$$E_n= \frac{3}{\sqrt 5\varphi^{n+1}}$$

Cette erreur tend exponentiellement vers 0 lorsque $n$ tend vers l'infini.

In [ ]:
def complexite_approchee1(n):
    phi = (1 + math.sqrt(5)) / 2
    return 3 * phi ** (n + 1) / math.sqrt(5) - 3

Voici par exemple une valeur approchée du nombre d'opérations effectuées lors du calcul de $d_{32}$.

In [ ]:
print(complexite_approchee1(32))

Vérifions ...

In [ ]:
cptr0.reset()
d = nb_der1(32)
print(cptr0.val)

Eh oui, 10 MILLIONS d'opérations. Combien le calcul de $d_{100}$ demanderait-il d'opérations ?

In [ ]:
print(complexite_approchee1(100))

Inutile d'insister. À raison de 1 milliard d'opérations par seconde, il nous faudrait 54000 ans pour calculer $d_{100}$ (à un demi-millénaire près).

In [ ]:
complexite_approchee1(100) / 10 ** 9 / 86400 / 365

**Remarque.** On entend souvent dire que la complexité de la fonction est mauvaise parce qu'elle est récursive. **Ce n'est absolument pas le cas**. Ce qui rend la complexité terrifiante c'est une **mauvaise utilisation** de la récursivité.

### 1.2 Itérations intelligentes

La fonction `nb_der2` ci-dessous effectue clairement $3n$ opérations arithmétiques pour le calcul de $d_n$.

In [ ]:
def nb_der2(n, cptr=cptr0):
    u, v = 1, 0
    for k in range(n):
        cptr.incr(3)
        w = (k + 1) * (u + v)
        u, v = v, w
    return u

In [ ]:
for n in range(11):
    print('%3d%10d' % (n, nb_der2(n)))

In [ ]:
cptr0.reset()
d = nb_der2(100)
print(cptr0.val)
print(d)

Pour calculer $d_{100}$ avec `nb_der2`, il faut 0 seconde. En fait, ce n'est pas tout à fait vrai : il faut 50 millionièmes de seconde.

In [ ]:
t1 = time.time()
for k in range(100000):
    d = nb_der2(100)
t2 = time.time()
print('%5.1es' % ((t2 - t1)/100000))

La fonction `nb_der2` calcule sans souci $d_{10^4}$ qui possède ... combien de chiffres en base 10 ?

In [ ]:
sys.set_int_max_str_digits(100000)

In [ ]:
print(len(str(nb_der2(10000))))

On obtient en quelques secondes la valeur de $d_{10 ^5}$. Voir à la fin du notebook.

### 1.3 Mémoïsation

La fonction `nb_der3` ci-dessous effectue $3n - 3$ opérations arithmétiques pour le calcul de $d_n$. Cool, $3$ opérations de moins que `nb_der2` !

In [ ]:
def nb_der3(n, cptr=cptr0):
    D = (n + 1) * [0]
    D[0] = 1
    for k in range(n - 1):
        cptr.incr(3)
        D[k + 2] = (k + 1) * (D[k + 1] + D[k])
    return D

In [ ]:
for n in range(11):
    print('%3d%10d' % (n, nb_der3(n)[n]))

In [ ]:
cptr0.reset()
d = nb_der3(100)[100]
print(cptr0.val)
print(d)

*Oui, mais* ...

Où est le problème avec cette fonction ? C'est sa complexité *en espace*. On a $d_n\sim n!/e$. À quelques bits près, la *taille* de $d_n$ (c'est à dire la mémoire que ce nombre occupe) est $\lg d_n\sim \lg n!$.

<p style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;border-radius:10px;" >
<b>Proposition 3.</b> $\lg d_n= n\lg n - n\lg e +o(n)$
</p>

**Démonstration.** Par la formule de Stirling,

$$n!= n^n e^{-n}\sqrt{2\pi n}(1+o(1))$$

Un passage au logarithme nous donne un développement asymptotique à 4 termes de $\ln n!$, ce qui est bien plus que nous ne voulions.

$$\lg n!=n\lg n - n\lg e + \frac 1 2\lg n + \frac 1 2 \lg(2\pi) +o(1)=n\lg n - n\lg e + o(n)$$

<p style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;border-radius:10px;" >
    <b>Proposition 4.</b> Soient $\sum a_n$ et $\sum b_n$ deux séries divergentes à termes positifs. On suppose $a_n\sim b_n$. Alors, les sommes partielles sont équivalentes :<br>
$$\sum_{k=0}^n a_k\sim\sum_{k=0}^n b_k$$
</p>

**Démonstration.** Notons $S_n$ et $S'_n$ les sommes partielles des séries $\sum a_n$ et $\sum b_n$. Soit $\varepsilon>0$. Prenons de plus $\varepsilon<1$. Il existe $n_0\in\mathbb N$ tel que pour tout $k\ge n_0$,

$$(1-\varepsilon)b_k\le a_k\le(1+\varepsilon)b_k$$

Soit $n\ge n_0$. Prenons $n$ assez grand pour que $S'_n>0$. On a, en sommant l'inégalité ci-dessus pour $k\in[|n_0+1,n|]$,

$$(1-\varepsilon)(S'_n-S'_{n_0})\le S_n-S_{n_0}\le(1+\varepsilon)(S'_n-S'_{n_0})$$

$$(1-\varepsilon)\left(1-\frac{S'_{n_0}}{S'_n}\right)+\frac{S_{n_0}}{S'_n}\le \frac{S_n}{S'_n}\le(1+\varepsilon)\left(1-\frac{S'_{n_0}}{S'_n}\right)+\frac{S_{n_0}}{S'_n}$$

La série $\sum b_n$ diverge et est à termes positifs donc $S'_n$ tend vers $+\infty$ lorsque $n$ tend vers l'infini. Le minorant de l'inégalité ci-dessus tend ainsi vers $(1-\varepsilon$ lorsque $n$ tend vers l'infini. De là, pour tout $n$ assez grand, il est supérieur à $1-2\varepsilon$. De même, pour tout $n$ assez grand, le majorant est inférieur à $1+2\varepsilon$. Ainsi, pour tout $n$ assez grand,

$$1-2\varepsilon\le \frac{S_n}{S'_n}\le1+2\varepsilon$$

La liste $D$ occupe donc un espace mémoire qui est

$$M_n\sim\sum_{k=1}^n (k\lg k-k\lg e)\text{ bits}$$

<p style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;border-radius:10px;" >
    <b>Proposition 5</b>. $M_n\sim \frac 1 2 n^2\lg n-\frac 1 2n^2\lg e$
</p>

**Démonstration.** On a 

$$\sum_{k=1}^nk\lg e=\frac 1 2n(n+1)\lg e=\frac 1 2n^2\lg e+O(n)$$

Passons à la somme

$$S_n=\sum_{k=1}^n k\ln k$$
    
Comparaison séries-intégrales ! La fonction $x\longmapsto x\ln x$ est croissante sur $[1,+\infty[$. On a donc pour tout $k\in\mathbb N^*$ et tout $x\in[k,k+1]$,

$$k\ln k\le x\ln x\le(k+1)\ln(k+1)$$

De là,

$$k\ln k\le \int_k^{k+1}x\ln x\, dx\le(k+1)\ln(k+1)$$

Soit $n\ge 2$. Sommons pour $k$ allant de 1 à $n-1$ pour obtenir

$$S_{n-1}\le \int_1^{n}x\ln x\, dx\le S_n$$

et donc

$$\int_1^{n}x\ln x\, dx\le S_n\le\int_1^{n+1}x\ln x\, dx$$

Par une intégration par parties,

$$\int_1^{n}x\ln x\, dx=\frac 1 2n^2\ln n-\frac 1 2\int_1^nx\, dx=\frac 1 2n^2\ln n-\frac 1 4 n^2+\frac 1 4\sim \frac 1 2n^2\ln n$$

d'où facilement, comme dirait Aristide, le résultat. Il suffit de diviser par $\ln 2$ et de ... soustraire des équivalents. Passons sous silence ce léger détail :-).

La fonction `memoire` renvoie une estimation du nombre d'octets occupés par la liste $D$.

In [ ]:
def memoire(n):
    return n ** 2 * math.log(n, 2) / 16 - n ** 2 * math.log(math.e, 2) / 16

Tentons $d_{10^4}$. Que donne notre estimation ?

In [ ]:
print(memoire(10000))

Environ 74 Mo. Étant donné que nous avons fait des estimations à la va vite, quel est exactement l'espace occupé par $D$ ? Il est facile de l'obtenir avec la fonction `sys.getsizeof`.

In [ ]:
n = 10000
D = nb_der3(n)
m = sys.getsizeof(D)
for k in range(n + 1):
    m += sys.getsizeof(D[k])
print(m)

On a donc bien trèèès bien estimé. Pour en revenir à nos problèmes d'espace, ça passe pour $10^4$, mais quel gaspillage ! Nous ne pourrions pas calculer $d_{10^5}$, parce qu'il nous faudrait environ 9 Go ... que nous n'avons pas. Les ressources, c'est limité.

In [ ]:
print(memoire(10 ** 5) / 10 ** 9)

## 2. La formule sommatoire

<p style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;border-radius:10px;" >
    <b>Proposition 6 (formule sommatoire).</b> Pour tout $n\in\mathbb N$,
$$d_n=n!\sum_{k=0}^n\frac{(-1)^k}{k!}$$
</p>

Remarquons que

$$n!\sum_{k=0}^n\frac{(-1)^k}{k!}=\sum_{k=0}^n(-1)^k\frac{n!}{k!}=(-1)^n\sum_{k=0}^n(-1)^kn^{\underline{k}}$$


### 2.1 Boucle naïve $\implies$ mauvaise complexité

La fonction `power_dn`prend en paramètres un « nombre » $x$ et un entier $n$. Elle renvoie

$$x^{\underline n}=x(x-1)\ldots,(x-n+1)$$

Sa complexité en nombre d'opérations arithmétiques est $2n$.

In [ ]:
def power_dn(x, n, cptr=cptr0):
    p = 1
    for k in range(n):
        p = p * (x - k)
        cptr.incr(2)
    return p

In [ ]:
cptr0.reset()
a = power_dn(123, 17)
print(cptr0.val)
print(a)

La fonction `nb_der4` calcule naïvement $d_n$ à l'aide de la formule sommatoire. Dans le décompte des opérations, on ne compte pas les puissances de $-1$ qui pourraient être calculées bien plus intelligemment. On ne compte pas non plus les produits par $\pm 1$.

In [ ]:
def nb_der4(n, cptr=cptr0):
    s = 0
    for k in range(n + 1):
        s = s + (-1) ** k * power_dn(n, k, cptr)
        cptr.incr(1)
    if n % 2 == 0: return s
    else: return -s

In [ ]:
cptr0.reset()
d = nb_der4(100)
print(cptr0.val)
print(d)

Notons $C_n$ la complexité de `nb_der4`. On a

$$C_n=\sum_{k=0}^n(1+2k)=(n+1)^2\sim n^2$$

`nb_der4` est donc de complexité temporelle quadratique.

In [ ]:
def complexite4(n): return (n + 1) ** 2

In [ ]:
print(complexite4(100))

Il nous est impossible de calculer $d_{10^5}$ en un temps raisonnable avec la fonction `nb_der4` parce qu'il faudrait faire 10 MILLIARDS d'opérations.

In [ ]:
print(complexite4(10 ** 5))

### 2.2 Boucle intelligente $\implies$ bonne complexité

On peut utiliser la formule sommatoire pour écrire une fonction de complexité linéaire. Pour cela, il suffit de calculer « à la volée » les puissances descendantes. Dans le corps de la fonction `nb_der5` ci-dessous, la variable $p$ contient, à la ligne 6, $n^{\underline{k}}$. Comme pour `nb_der4` on ne décompte pas les puissances de $-1$ et les produits par $\pm 1$ dans les opérations.

In [ ]:
def nb_der5(n, cptr=cptr0):
    s = 0
    p = 1
    for k in range(n + 1):
        s = s + (-1) ** k * p
        p = p * (n - k)
        cptr.incr(3)
    if n % 2 == 0: return s
    else: return -s

In [ ]:
for n in range(11):
    print('%3d%10d' % (n, nb_der5(n)))

La complexité de cette fonction est clairement $3(n+1)$. Le calcul de $d_{100}$ demande $3\times101=303$ opérations.

In [ ]:
cptr0.reset()
d = nb_der5(100)
print(cptr0.val)
print(d)

## 3. Récurrence ou formule sommatoire ?

Le nombre d'opérations n'est pas la fin de l'histoire. Le *type* des opérations et la *taille* des entiers sur lesquels on opère ont aussi de l'importance.

Faisons juste un test. Calculons $d_{10^5}$. Comme nous l'avons vu, les fonctions `nb_der1`, `nb_der3` et `nb_der4` en sont incapables.

Comparons les temps mis par `nb_der2` et `nb_der5`.

In [ ]:
t1 = time.time()
d = nb_der2(100000)
t2 = time.time()
print('%5.1fs' % (t2 - t1))

In [ ]:
t1 = time.time()
d = nb_der5(100000)
t2 = time.time()
print('%5.1fs' % (t2 - t1))

<p style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;border-radius:10px;" >
    <b>Théorème 7.</b> J'achète sans hésiter <font face="monospace">nb_der2</font>.
</p>